# Início

In [1]:
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import pandas as pd
import copy
from tqdm import tqdm
import time
import os
from scipy import signal
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score
from sklearn.decomposition import PCA
from natsort import natsorted

In [2]:
files = ['acc_climbingup_forearm.csv',
         'acc_climbingup_waist.csv',
         'acc_walking_forearm.csv',
         'acc_walking_waist.csv']
s = [None] * len(files)
for i, path in enumerate(files):
    data = pd.read_csv(path)
    s[i] = data['attr_x'].to_numpy()
    s[i] = s[i][:26938]
    s[i] = s[i] - s[i].mean()


In [3]:
fig = go.Figure()
for i, x in enumerate(s):
    fig.add_trace(go.Scatter(y=x, mode="lines", showlegend=True, name=files[i]))
fig.show()

In [6]:
def picotar(x, J, passo):
    N = x.shape[0]
    Nj = (N-J)//passo + 1
    X = np.zeros((Nj, J))
    for i in range(Nj):
        X[i,:] = x[(i*passo):(i*passo+J)]
    return X

In [11]:
def pcabase(X):
    M = np.ones((X.shape[0],1)).dot(X.mean(axis=0).reshape(1,X.shape[1]))
    R = (X-M).transpose().dot(X-M)
    l, vet = np.linalg.eig(R)
    inds = np.argsort(l)
    vet = vet[:,inds][:,::-1]
    return l, vet

In [12]:
J = 150
passo = 75
X = picotar(s[0], J, passo)
l, vet = pcabase(X)

In [13]:
fig = px.line(vet[:,:5], range_y=[-1/5,1/5])
fig.show()
fig = px.scatter(l.cumsum()/l.sum(), range_y=[0,1.1])
fig.show()

In [46]:
d = 30
W = vet[:,:d]

In [49]:
i = 1000
X = picotar(s[2], J)
x = X[i,:]
S = x.dot(W)
xh = S.dot(W.transpose())
fig = px.line(xh)
fig.add_trace(go.Scatter(y=x, mode='lines', showlegend=True))

In [ ]:
class MLP(nn.Module):
    def __init__(self):
        super().__init__()

        self.all_layers = torch.nn.Sequential(

            # 1st hidden layer
            nn.Flatten(start_dim=1),
            nn.Linear(300, 100),
            nn.Tanh(),

            # 2nd hidden layer
            nn.Linear(100, 2)
            # nn.Softmax(dim=1),

#             # output layer
#             nn.Linear(15, num_classes),
        )

    def forward(self, x):
        logits = self.all_layers(x)
        return logits

In [ ]:
def ajusteDados(X):
    N = X.shape[0]
    Nj = X.shape[2]
    S = np.zeros((N*(Nj-151), 2, 150))
    y = np.zeros((N*(Nj-151), 2))
    for i in range(N):
        for j in range(Nj-151):
            S[(i*(Nj-151)+j),:,:] = X[i,:,j:(j+150)]
            y[(i*(Nj-151)+j),:] = X[i,:,(j+150)]
    return S, y

In [ ]:
def predlin(dados, ordem):
    N = dados.shape[0]
    X = dados[:,:1200].reshape(N,2,600) / 50   # Normalizando para a faixa de -1 a 1 aprox.
    y = dados[:,-1]
    X_train, X_test, y_train, y_test = train_test_split(
        X, y, test_size=0.2, random_state=1, stratify=y)

    X_train, X_val, y_train, y_val = train_test_split(
        X_train, y_train, test_size=0.1, random_state=1, stratify=y_train)
    
    X_train, s_train = ajusteDados(X_train)
    X_val, s_val = ajusteDados(X_val)
    X_test, s_test = ajusteDados(X_test)
    
    aux = np.linalg.inv(np.matmul(X_train[:,0,-ordem:].transpose(), X_train[:,0,-ordem:]))
    w1 = np.matmul(np.matmul(aux, X_train[:,0,-ordem:].transpose()), s_train[:,0])
    
    aux = np.linalg.inv(np.matmul(X_train[:,1,-ordem:].transpose(), X_train[:,1,-ordem:]))
    w2 = np.matmul(np.matmul(aux, X_train[:,1,-ordem:].transpose()), s_train[:,1])

    return w1, w2

In [ ]:
ordem = 12
w1, w2 = predlin(D[3], ordem)

# Exp 1

In [71]:
files

['acc_climbingup_forearm.csv',
 'acc_climbingup_waist.csv',
 'acc_walking_forearm.csv',
 'acc_walking_waist.csv']

In [74]:
Xtr1 = np.concatenate((picotar(s[0][-10000:], J), picotar(s[2][-10000:], J)))
Xtr2 = np.concatenate((picotar(s[1][-10000:], J), picotar(s[3][-10000:], J)))
Xte1 = np.concatenate((picotar(s[0][:10000], J), picotar(s[2][:10000], J)))
Xte2 = np.concatenate((picotar(s[1][:10000], J), picotar(s[3][:10000], J)))
N = Xtr1.shape[0]
y = (np.arange(N)<N//2).astype(int)

In [77]:
l, vet = pcabase(Xtr1)
fig = px.line(vet[:,:5], range_y=[-1/5,1/5])
fig.show()
fig = px.scatter(l.cumsum()/l.sum(), range_y=[0,1.1])
fig.show()

In [79]:
d = 60
W = vet[:,:d]
Str1 = Xtr1.dot(W)
Str2 = Xtr2.dot(W)
Ste1 = Xte1.dot(W)
Ste2 = Xte2.dot(W)

In [102]:
neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(Str1, y)
y_pred = neigh.predict(Ste1)
accuracy_score(y, y_pred)

0.8026395939086295

In [103]:
neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(Xtr1, y)
y_pred = neigh.predict(Xte1)
accuracy_score(y, y_pred)

0.8084263959390863

In [100]:
x = Xtr2[0,:]
xh = x.dot(W).dot(W.transpose())

fig = px.line(x)
fig.add_trace(go.Scatter(y=xh, mode='lines', showlegend=True))

In [101]:
c = np.correlate(x, x, 'full')
px.line(c[-len(c)//2:])

In [97]:
Ctr1 = np.zeros_like(Xtr1)
Ctr2 = np.zeros_like(Xtr2)
Cte1 = np.zeros_like(Xte1)
Cte2 = np.zeros_like(Xte2)
for i in range(Cte1.shape[0]):
    Ctr1[i,:] = np.correlate(Xtr1[i,:], Xtr1[i,:], 'full')[-150:]
    Ctr2[i,:] = np.correlate(Xtr2[i,:], Xtr2[i,:], 'full')[-150:]
    Cte1[i,:] = np.correlate(Xte1[i,:], Xte1[i,:], 'full')[-150:]
    Cte2[i,:] = np.correlate(Xte2[i,:], Xte2[i,:], 'full')[-150:]
    

In [99]:
neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(Xtr1, y)
y_pred = neigh.predict(Xte1)
accuracy_score(y, y_pred)

0.8084263959390863

In [109]:
px.scatter(x=Str1[:,0], y=Str1[:,1], color=y.astype(str))